<a href="https://colab.research.google.com/github/kmsekgothe/load-shortfall-regression-predict-api/blob/master/KaggleNotebook.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Team 12 - Advanced Classification Predict

© Explore Data Science Academy

---

### Introduction: 
---

### Predict Overview




<a id="cont"></a>

## Table of Contents

<a href=#one>1. Importing Packages</a>

<a href=#two>2. Loading Data</a>

<a href=#three>3. Exploratory Data Analysis (EDA)</a>

<a href=#four>4. Data Engineering</a>

<a href=#five>5. Modeling</a>

<a href=#six>6. Model Performance</a>

<a href=#seven>7. Model Explanations</a>

 <a id="one"></a>
## 1. Importing Packages

In this section we import the necessary libraries needed for Data Analysis, Data Manipulation, Data Visualization and Model Building.

In [1]:
# libraries needed for Data Analysis and  Data Manipulation
import numpy as np # used to evaluate arrays
import pandas as pd # used to create and utilise tabular data ie Pandas DataFrame

# libraries to be used for Data Visualization
import matplotlib.pyplot as plt # used to visualize data
import seaborn as sns # used to visualize data
from matplotlib import rc
%matplotlib inline

# Libraries for data preparation and model building
import sklearn
import re
from nltk.corpus import stopwords
from nltk.tokenize import TreebankWordTokenizer
from nltk.stem import WordNetLemmatizer
import string
import requests
from time import sleep
from nltk.corpus import stopwords
from wordcloud import WordCloud

from sklearn.feature_extraction.text import CountVectorizer
from sklearn import preprocessing
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import roc_auc_score
from sklearn.metrics import recall_score
from sklearn.metrics import precision_score
from sklearn.metrics import f1_score
from sklearn import metrics
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from sklearn.linear_model import LogisticRegression
from sklearn.feature_selection import SelectKBest
from sklearn.model_selection import RandomizedSearchCV, GridSearchCV

# Suppress cell warnings
import warnings
warnings.filterwarnings("ignore")

In [ ]:
# !pip install wordcloud

<a id="two"></a>
## 2. Loading the Data
<a class="anchor" id="1.1"></a>
<a href=#cont>Back to Table of Contents</a>

- Loading of Test and Train datasets. 
- Concatenate the datasets to ensure Data Engineering is done only once (for convenience). 
- Dataframes will then be split later on when needed.

In [14]:
df = pd.read_csv('train.csv') # load the data
df_test = pd.read_csv('test_with_no_labels.csv')
pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', None)

Perform basic analysis on the dataframe.

In [15]:
# Basic Train Analysis

df.shape # train DataFrame has 15 819 rows and 3 columns

(15819, 3)

In [ ]:
df.head()

In [ ]:
df.info()

In [21]:
df['sentiment'].unique()

15819

In [ ]:
df['sentiment'].value_counts().plot(kind = 'bar')
plt.title('Class Frequency')
plt.xlabel('Class')
plt.ylabel('Frequency')
plt.show()

In [ ]:
unique, counts = np.unique(df['sentiment'], return_counts=True)
unique_counts_dict = {'Unique Count':
             {
                 "Class -1": counts[0],
                "Class 0": counts[1],
              "Class 1": counts[2],
              "Class 2": counts[3]
              }
             }
unique_count = pd.DataFrame(data=unique_counts_dict)
unique_count.sort_values(by='Unique Count', ascending=False)

Class Description:

- 2 News: the tweet links to factual news about climate change
- 1 Pro: the tweet supports the belief of man-made climate change
- 0 Neutral: the tweet neither supports nor refutes the belief of man-made climate change
- -1 Anti: the tweet does not believe in man-made climate change

Note the imbalance here: there are over 8000 observations in class 1 and only 1296 observations in class -1.

In [ ]:
# Basic Test Analysis

df_test.shape # test DataFrame has 10 546 rows and 2 columns

In [ ]:
df_test.head()

In [ ]:
df_test.info()

<a id="three"></a>
## 3. Data Preprocessing
<a class="anchor" id="1.1"></a>
<a href=#cont>Back to Table of Contents</a>

#### Data Cleaning and Formatting
 

Before we can do **Exploratory Data Analysis** (EDA) in section 4, we need to ensure that our data is in the correct format that can actually be used.

In [ ]:
df.head()

In [13]:
# Better view of what's in the dataset
for i, row in df.iterrows():
    print(i)
    print(row)
    print("\n")

0
sentiment                                                                                                                         1
message      PolySciMajor EPA chief doesn't think carbon dioxide is main cause of global warming and.. wait, what!?   via @mashable
tweetid                                                                                                                      625221
url                                                                                                     ['https://t.co/yeLvcEFXkC']
Name: 0, dtype: object


1
sentiment                                                                 1
message      It's not like we lack evidence of anthropogenic global warming
tweetid                                                              126103
url                                                                      []
Name: 1, dtype: object


2
sentiment                                                                                                       

Name: 291, dtype: object


292
sentiment                                                       0
message      Stand up for all of the successes of climate change:
tweetid                                                    424186
url                                                            []
Name: 292, dtype: object


293
sentiment                                                                                                                                             1
message      RT @Fusion: America is about to become the only country in the world with a leader who doesnÃ¢â‚¬â„¢t think global warming is real.Ã¢â‚¬Â¦
tweetid                                                                                                                                          150591
url                                                                                                                                                  []
Name: 293, dtype: object


294
sentiment                          

Name: 505, dtype: object


506
sentiment                                                                                                                                          -1
message      RT @DineshDSouza: THOUGHT FOR THE DAY: If gender is a social construct--which is to say 'all in your head'-- maybe climate change is too
tweetid                                                                                                                                        408538
url                                                                                                                                                []
Name: 506, dtype: object


507
sentiment                                       1
message      11 terrifying climate change facts  
tweetid                                    551452
url                   ['https://t.co/JgUosRxVlf']
Name: 507, dtype: object


508
sentiment                                                                                                  

779
sentiment                                                                                                                                         0
message      RT @TheCosby: How you gonna post this without an @, an IG, a snap, her location, her views on climate change &amp; BLM, her type, wha…
tweetid                                                                                                                                       58911
url                                                                                                                                              []
Name: 779, dtype: object


780
sentiment                                                                                                 0
message      The 'skeptical environmentalist' takes on climate change in the controversial doc, Cool It    
tweetid                                                                                               46988
url                                              


964
sentiment                                                                                                                               1
message      We can chose to be on the right side of history on climate change or we can be catastrophically wrong. It's real. AÃ¢â‚¬Â¦  
tweetid                                                                                                                            205010
url                                                                                                           ['https://t.co/qB9uXqmcur']
Name: 964, dtype: object


965
sentiment                                                                                                1
message      I just joined @NatGeoChannel @21CF in combating climate change. Take action #BeforeTheFlood  
tweetid                                                                                             990854
url                                                                            ['https://t.

...

sentiment                                                                                                                        2
message      The global seed vault in Spitsbergen is threatened by climate change. Piqd by #AndreaChu. Article by @dpcarrington…  
tweetid                                                                                                                     957691
url                                                                                                    ['https://t.co/lcEhKMhvNU']
Name: 14726, dtype: object


14727
sentiment                                                                                                                                     1
message      RT @ajplus: With no climate change leadership in the White House, can entrepreneurs and green energy companies redeem the U.S.?  …
tweetid                                                                                                                                  263169
url      

Name: 14987, dtype: object


14988
sentiment                                                                                                                                               1
message      RT @joshgad: The mourning stage is over. Now we fight. Putting a climate change denier as head of EPA is an act of war on our kids. #StandUp
tweetid                                                                                                                                             88476
url                                                                                                                                                    []
Name: 14988, dtype: object


14989
sentiment                                                                                       2
message      EPA chief: Carbon dioxide not 'primary contributor' to climate change @CNNPolitics  
tweetid                                                                                    186608
url                 

sentiment                                                                                                                                                   0
message      ÃƒÂ¨ online la nuova versione de #ilfoglio si proprio quello il cui direttore dice che il global warming non esiste perchÃƒÂ¨ a Cortina si scia.
tweetid                                                                                                                                                122061
url                                                                                                                                                        []
Name: 15259, dtype: object


15260
sentiment                                                                                                                                                       1
message      RT @1followernodad: parent: I'd do anything for my children!\n\nScientist: here's how to stave off climate change so your children can stay oÃ¢â‚¬Â¦
tweetid  

sentiment                                                                           1
message      Can Australia's wicked heat wave convince climate change deniers? - DW  
tweetid                                                                        240595
url                                                       ['https://t.co/5KFhn7s7kH']
Name: 15486, dtype: object


15487
sentiment                                                                                                                                1
message      RT @ClimateReality: Watch @Schwarzenegger go to the frontlines to learn about the links between climate change and wildfires…
tweetid                                                                                                                             734632
url                                                                                                                                     []
Name: 15487, dtype: object


15488
sentiment                     

sentiment                                                                                                                            0
message      RT @stinson: All those 'After Trump, China takes the lead in fighting climate change' pieces have to confront reality.  …
tweetid                                                                                                                         240504
url                                                                                                          ['https://t.co/xzYW6IK…']
Name: 15765, dtype: object


15766
sentiment                                          0
message      @Cerb32 Are you a global warming shill?
tweetid                                       277693
url                                               []
Name: 15766, dtype: object


15767
sentiment                                                                                                                                 0
message      RT @Advil: so @pitbull ju

In [3]:
df.head()

sentiment  \
0          1   
1          1   
2          2   
3          1   
4          1   

                                                                                                                                        message  \
0  PolySciMajor EPA chief doesn't think carbon dioxide is main cause of global warming and.. wait, what!? https://t.co/yeLvcEFXkC via @mashable   
1                                                                                It's not like we lack evidence of anthropogenic global warming   
2  RT @RawStory: Researchers say we have three years to act on climate change before it’s too late https://t.co/WdT0KdUr2f https://t.co/Z0ANPT…   
3                                           #TodayinMaker# WIRED : 2016 was a pivotal year in the war on climate change https://t.co/44wOTxTLcD   
4                    RT @SoyNovioDeTodas: It's 2016, and a racist, sexist, climate change denying bigot is leading in the polls. #ElectionNight   

   tweetid  
0   625221  
1   126103  
2   698562  
3   573736  
4   466954

In [4]:
# Create new column, data = linkedembedded urls from message column

def extract_urls(string):
    url_pattern = r"(?i)\b((?:https?://|www\d{0,3}[.]|[a-z0-9.\-]+[.][a-z]{2,4}/)(?:[^\s()<>]+|\(([^\s()<>]+|(\([^\s()<>]+\)))*\))+(?:\(([^\s()<>]+|(\([^\s()<>]+\)))*\)|[^\s`!()\[\]{};:'\".,<>?«»“”‘’]))"
    url = re.findall(url_pattern, string)      
    return str([x[0] for x in url])

df['url']  = df['message'].apply(extract_urls)

In [5]:
url_pattern = r'http[s]?://(?:[A-Za-z]|[0-9]|[$-_@.&+]|[!*\(\),]|(?:%[0-9A-Fa-f][0-9A-Fa-f]))+'
df['message'] = df['message'].replace(to_replace = url_pattern, value = r' ', regex = True)
df

sentiment  \
0              1   
1              1   
2              2   
3              1   
4              1   
...          ...   
15814          1   
15815          2   
15816          0   
15817         -1   
15818          0   

                                                                                                                                            message  \
0                            PolySciMajor EPA chief doesn't think carbon dioxide is main cause of global warming and.. wait, what!?   via @mashable   
1                                                                                    It's not like we lack evidence of anthropogenic global warming   
2                                              RT @RawStory: Researchers say we have three years to act on climate change before it’s too late    …   
3                                                                     #TodayinMaker# WIRED : 2016 was a pivotal year in the war on climate change     
4                        RT @SoyNovioDeTodas: It's 2016, and a racist, sexist, climate change denying bigot is leading in the polls. #ElectionNight   
...                                                                                                                                             ...   
15814  RT @ezlusztig: They took down the material on global warming, LGBT rights, and health care. But now they're hocking Melania's QVC. https://…   
15815                                             RT @washingtonpost: How climate change could be breaking up a 200-million-year-old relationship     
15816                         notiven: RT: nytimesworld :What does Trump actually believe about climate change? Rick Perry joins other aides in …     
15817             RT @sara8smiles: Hey liberals the climate change crap is a hoax that ties to #Agenda2030.\nThe Climate is Being Changed byÃ¢â‚¬Â¦   
15818                                                              RT @Chet_Cannon: .@kurteichenwald's 'climate change equation' in 4 screenshots     

       tweetid                                                  url  
0       625221                          ['https://t.co/yeLvcEFXkC']  
1       126103                                                   []  
2       698562  ['https://t.co/WdT0KdUr2f', 'https://t.co/Z0ANPT…']  
3       573736                          ['https://t.co/44wOTxTLcD']  
4       466954                                                   []  
...        ...                                                  ...  
15814    22001                                                   []  
15815    17856                          ['https://t.co/rPFGvb2pLq']  
15816   384248                                ['https://t.co/0Mp2']  
15817   819732                                                   []  
15818   806319                          ['https://t.co/lp7UufcxDQ']  

[15819 rows x 4 columns]

In [7]:
#why is there a url in message column?!
df['message'][15814]

"RT @ezlusztig: They took down the material on global warming, LGBT rights, and health care. But now they're hocking Melania's QVC. https://…"

In [ ]:
df['url'] = df['url'].astype(str).str[1:-1]

In [ ]:
df['url'] = df['url'].str.replace("'", "")

In [ ]:
df

In [10]:
# Extract sentiment information from urls. i.e. web page titles.

def extract_web_title(url):
    if len(url) > 0:
        params = {'headers':'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:51.0) Gecko/20100101 Firefox/51.0'}
        get_url = requests.get(url, headers=params) # Sends a GET request
        url_text = get_url.text
        return url_text[url_text.find('<title>') + 7 : url_text.find('</title>')]

In [12]:
extract_web_title('https://t.co/yeLvcEFXkC')

'EPA chief denies carbon dioxide is main cause of global warming and... wait, what!?'

In [11]:
df['url'] = df['url'].apply([extract_web_title(x) for x in df['url']])

InvalidSchema: No connection adapters were found for "['https://t.co/yeLvcEFXkC']"

In [ ]:
extract_web_title("https://t.co/yeLvcEFXkC")

#### Clean data

In [ ]:
# Remove special characters

def clean_data(tweet):
    pattern_url = r'http[s]?://(?:[A-Za-z]|[0-9]|[$-_@.&+]|[!*\(\),]|(?:%[0-9A-Fa-f][0-9A-Fa-f]))+'
    tweet = re.sub(pattern_url, '', tweet) 
    tweet = re.sub(r'@[A-Za-z0-9]+', '', tweet)
    tweet = re.sub(r'#', '', tweet)
    tweet = re.sub(r'RT[\s]+', '', tweet)
    return tweet

In [ ]:
df['clean_tweet'] = df['message'].apply(clean_data)

In [ ]:
# Remove punctuation

def remove_punctuation(tweet):
    return ''.join([l for l in tweet if l not in string.punctuation])

In [ ]:
df['clean_tweet'] = df['clean_tweet'].apply(remove_punctuation)

In [ ]:
# Make all the text lower case to remove some noise from capitalisation

def remove_cap(tweet):
    return tweet.lower()

df['clean_tweet'] = df['clean_tweet'].apply(remove_cap)

In [ ]:
tokeniser = TreebankWordTokenizer()
df['clean_tweet'] = df['clean_tweet'].apply(tokeniser.tokenize)

In [ ]:
df.head()

In [ ]:
# Lemmetize the words in the dataframe

def lemma(words, lemmatizer):
    return [lemmatizer.lemmatize(word) for word in words]   

In [ ]:
lemmatizer = WordNetLemmatizer()
df['clean_tweet'] = df['clean_tweet'].apply(lemma, args=(lemmatizer, ))

In [ ]:
df.head()

In [ ]:
df['clean_tweet'] = df['clean_tweet'].map

In [ ]:
# Remove stopwords

#def remove_stop_words(tokens):    
#    return [t for t in tokens if t not in stopwords.words('english')]

#df['clean_tweet'] = df['clean_tweet'].apply(remove_stop_words)

#### Data Cleaning and Formatting Summary

- 

<a id="four"></a>
## 4. Exploratory Data Analysis (EDA)
<a class="anchor" id="1.1"></a>
<a href=#cont>Back to Table of Contents</a>

Exploratory Data Analysis refers to the critical process of performing initial investigations on data so as to discover patterns, to spot anomalies, to check assumptions with the help of summary statistics and graphical representations.
The following section analyses and provides an overview of the given data

In [ ]:
# Visualize the frequent words
#all_words = " ".join([sentence for sentence in df['clean_tweet']])
#df['clean_tweet'] = ''.join(map(str, df['clean_tweet']))
#wordcloud = WordCloud(width=800, height=500, random_state=42, max_font_size=100).generate(df['clean_tweet'])
df
# plot the graph
#plt.figure(figsize=(15,8))
#plt.imshow(wordcloud, interpolation='bilinear')
#plt.axis('off')
#plt.show()

#### Key Insights

- 


<a id="five"></a>
## 5. Data Engineering
<a class="anchor" id="1.1"></a>
<a href=#cont>Back to Table of Contents</a>

Create targets and features dataframes then seperate the test from the train data set.

In [ ]:
# feature extraction

vector = CountVectorizer(max_df=0.90, min_df=2, max_features=1000, stop_words=None, ngram_range=(1, 3)) #max_df=0?
X = vector.fit_transform(df['message'])
y = df['sentiment']

In [ ]:
# create targets and features dataset
#y =  df['sentiment']
#X = df.drop('sentiment', axis=1)

X = our features or independant variables (IVs). These will be used to predict our depedant variable. 

Y = dependant/target variable is also known as the dependent variable (DV) and is the target variable we want to predict.

In [ ]:
# split the train data further into train/test data (to perform validation before bringing in the true unseen test data)

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=50, shuffle=False)

### Feature Scaling

In [ ]:
#scaler = preprocessing.MinMaxScaler()
#X_scaled = scaler.fit_transform(X)

<a id="six"></a>
## 6. Modelling
<a class="anchor" id="1.1"></a>
<a href=#cont>Back to Table of Contents</a>

This section takes us through the machine learning process. We train and test a number of regression model algorithms and later select the model with the best performance to be used in this project. From the five modeling techniques, we compare the RMSE values of each model as well as the time taken to train and test each model. This will inform our model selection decision.

#### Model 1 - Logistic Regression

In [ ]:
# Training
model = LogisticRegression()
model.fit(X_train, y_train)

#### Model 2

#### Model 3

#### Model 4 

<a id="six"></a>
## 6. Model Performance
<a class="anchor" id="1.1"></a>
<a href=#cont>Back to Table of Contents</a>

In [ ]:
pred = model.predict(X_test)

In [ ]:
print('Classification Report')
print(classification_report(y_test, pred))

<a id="seven"></a>
## 7. Model Explanations
<a class="anchor" id="1.1"></a>
<a href=#cont>Back to Table of Contents</a>



##### XGBoost Regression

This section discusses the inner workings of the best performing model in a simple way.

## Conclusion

Given two datasets, train and test data, we were tasked with following the data science process. 

We first set out to understand the data and it's space, in other words, we set out to understand the electricity shortfall in Spain, the various variables that may or may not be correlated to the load shortfall in Spain, understanding the reasons behind the correlations or a lack thereof etc. We were presented with a lot of information and our first task was making sure we had a good understanding of the relevant things coming from the data. 

In our data, we saw null values we had to impute, we encountered unusable data types we needed to transfrom, and data falling in large ranges which we had to scale. All of this formed part of the iterative process of Data Preprocessing, Exploratorty Data Analysis and Data Engineering.

Essentially, we set out to understand and transform the data so that we may build an appropriate model that would best predict the load shortfall. 

We then built a few models then selected the right model out of these models, following an iterative train-validation process. The main model performance metric was the Root Mean Squared Error (RMSE), looking for the model that produced the lowerst RMSE value.

At this point, we have addressed the problem statement. In future, when given various cirsumstances (predictor observations) we are now able to predict the corresponding load shortfall with an average error (RMSE) of approximately 4300 (same units as the predicted variable, i.e. load shortfall).

#### Kaggle submission file
This section creates the Kaggle submission file in csv format.

In [ ]:
df.head()

In [ ]:
df_test.head()

In [ ]:
x_train_final = df['message']
x_test_final = df_test['message']

In [ ]:
vector = CountVectorizer(max_df=0.90, min_df=2, max_features=1000, stop_words=None, ngram_range=(1, 3)) #max_df=0?
x_train_final = vector.fit_transform(df['message'])
x_test_final = vector.fit_transform(df_test['message'])
y = df['sentiment']

In [ ]:
model.fit(x_train_final, y)

In [ ]:
predict_final = model.predict(x_test_final)

In [ ]:
daf = pd.DataFrame(predict_final, columns=['sentiment'])
daf.head()

In [ ]:
df_test_final = pd.read_csv('test_with_no_labels.csv')

In [ ]:
output = pd.DataFrame({"TweetID":df_test_final['tweetid']})
submission = output.join(daf)        
submission.to_csv("submission.csv", index=False)

In [ ]:
submission